In [22]:
from langchain.document_loaders import DirectoryLoader, PyPDFLoader
import os
from PyPDF2 import PdfReader
from langchain.text_splitter import CharacterTextSplitter
import json
from langchain.embeddings import OpenAIEmbeddings, HuggingFaceInstructEmbeddings
from langchain.vectorstores import FAISS
import pickle


In [4]:
loader = DirectoryLoader('pdfs/', glob="./*.pdf", loader_cls=PyPDFLoader)

In [5]:
print(loader.load())

[Document(page_content='CBAHISAUDI CENTRAL BOARD FOR  ACCREDITATION OF  HEALTHCARE INSTITUTIONS NATIONAL\nPrimary\nHealthcare\nSTANDARDS  \nEﬀective\nFeb. 20171.1 Edition  \n اﻟﻤﻌﺎﻳﻴﺮ اﻟﻮﻃﻨﻴﺔ\nﻟﻤﺮاﻛﺰ اﻟﺮﻋﺎﻳﺔ اﻟﺼﺤﻴﻪ اﻻوﻟﻴﺔ', metadata={'source': 'pdfs/CBAHI-PHC-Standards v1.1 Effective Feb.2017.pdf', 'page': 0}), Document(page_content=' \n2 |  \n \nThe mission of the Saudi Central Board for Accreditation of Healthcare Institutions (CBAHI) is to continuously \nimprove the safety and quality of healthcare services in the Kingdom of Saudi Arabia by supporting the \nhealthcare facilities to continuously comply with the accreditation standards. CBAHI does this through the \nprovision of preparation, on -site assessment, monitoring, education, publications and consultation services.  \nCBAHI is making every possible effort to separate its consultative and educational programs as well as all \npublications it produces from its accreditation activities. This manual i s produced for the sole use 

In [22]:
def get_pdf_text():
    text = ""
    directory_pdf = 'pdfs/'
    pdf_docs = os.listdir(directory_pdf)
    for pdf in pdf_docs:
        if pdf.endswith('.pdf'):
            print(pdf)
            pdf_reader = PdfReader(directory_pdf+pdf)
            for page in pdf_reader.pages:
                text += page.extract_text()
    with open('pdfs/output.txt', 'w') as file:
        file.write(text)
    return text


raw_text = get_pdf_text()

CBAHI-PHC-Standards v1.1 Effective Feb.2017.pdf
DENTAL CBAHI.pdf
CBAHI Ambulatory 2019.pdf
CBAHI 4TH EDITION National Healthcare Priorities.pdf
NATIONAL STANDARDS FOR ACUTE CORONARY SYNDROME SER_240115_145528.pdf
VTE REVISED POLICY - VERSION 5.pdf


In [20]:
# print(raw_text)

In [6]:
def get_text_chunks():
    text = open('pdfs/output.txt', 'r').read()
    text_splitter = CharacterTextSplitter(
        separator="\n",
        chunk_size=1000,
        chunk_overlap=200,
        length_function=len
    )
    chunks = text_splitter.split_text(text)
    print("lenghth of chunks ",len(chunks))
    print(type(chunks))
    return chunks

text_chunks = get_text_chunks()

Created a chunk of size 2772, which is longer than the specified 1000
Created a chunk of size 2477, which is longer than the specified 1000
Created a chunk of size 2606, which is longer than the specified 1000
Created a chunk of size 2897, which is longer than the specified 1000
Created a chunk of size 4434, which is longer than the specified 1000
Created a chunk of size 4190, which is longer than the specified 1000
Created a chunk of size 4645, which is longer than the specified 1000
Created a chunk of size 3941, which is longer than the specified 1000
Created a chunk of size 3990, which is longer than the specified 1000
Created a chunk of size 3334, which is longer than the specified 1000
Created a chunk of size 4020, which is longer than the specified 1000
Created a chunk of size 3522, which is longer than the specified 1000
Created a chunk of size 3578, which is longer than the specified 1000
Created a chunk of size 4413, which is longer than the specified 1000
Created a chunk of s

lenghth of chunks  1611
<class 'list'>


In [7]:
### To save the chunk into text 
def save_chunks_to_text_file(chunks, filename):
    with open(filename, 'w') as file:
        for chunk in chunks:
            file.write(chunk + '\n')

# Assuming text_chunks is your list of chunks
save_chunks_to_text_file(text_chunks, 'pdfs/chunks.txt')


In [1]:
def load_chunks_from_text_file(filename):
    with open(filename, 'r') as file:
        return file.read().splitlines()

loaded_chunks = load_chunks_from_text_file('pdfs/chunks.txt')
print(loaded_chunks)

['CBAHISAUDI CENTRAL BOARD FOR  ACCREDITATION OF  HEALTHCARE INSTITUTIONS NATIONAL', 'Primary', 'Healthcare', 'STANDARDS  ', 'Eﬀective', 'Feb. 20171.1 Edition  ', ' اﻟﻤﻌﺎﻳﻴﺮ اﻟﻮﻃﻨﻴﺔ', 'ﻟﻤﺮاﻛﺰ اﻟﺮﻋﺎﻳﺔ اﻟﺼﺤﻴﻪ اﻻوﻟﻴﺔ ', '2 |  ', ' ', 'The mission of the Saudi Central Board for Accreditation of Healthcare Institutions (CBAHI) is to continuously ', 'improve the safety and quality of healthcare services in the Kingdom of Saudi Arabia by supporting the ', 'healthcare facilities to continuously comply with the accreditation standards. CBAHI does this through the ', 'provision of preparation, on -site assessment, monitoring, education, publications and consultation services.  ', 'CBAHI is making every possible effort to separate its consultative and educational programs as well as all ', 'publications it produces from its accreditation activities. This manual i s produced for the sole use of the ', 'individual healthcare facilities and healthcare professionals in Saudi Arabia. CBAHI provides su

In [8]:
# to save it as json
def save_chunks(chunks, filename):
    with open(filename, 'w') as file:
        json.dump(chunks, file)

save_chunks(text_chunks, 'pdfs/chunks.json')

In [9]:
def load_chunks(filename):
    with open(filename, 'r') as file:
        return json.load(file)

loaded_chunks = load_chunks('pdfs/chunks.json')
print(type(loaded_chunks))

<class 'list'>


In [10]:
loaded_chunks = load_chunks('pdfs/chunks.json')
print(loaded_chunks)

['CBAHISAUDI CENTRAL BOARD FOR  ACCREDITATION OF  HEALTHCARE INSTITUTIONS NATIONAL\nPrimary\nHealthcare\nSTANDARDS  \nEﬀective\nFeb. 20171.1 Edition  \n اﻟﻤﻌﺎﻳﻴﺮ اﻟﻮﻃﻨﻴﺔ\nﻟﻤﺮاﻛﺰ اﻟﺮﻋﺎﻳﺔ اﻟﺼﺤﻴﻪ اﻻوﻟﻴﺔ \n2 |  \n \nThe mission of the Saudi Central Board for Accreditation of Healthcare Institutions (CBAHI) is to continuously \nimprove the safety and quality of healthcare services in the Kingdom of Saudi Arabia by supporting the \nhealthcare facilities to continuously comply with the accreditation standards. CBAHI does this through the \nprovision of preparation, on -site assessment, monitoring, education, publications and consultation services.  \nCBAHI is making every possible effort to separate its consultative and educational programs as well as all \npublications it produces from its accreditation activities. This manual i s produced for the sole use of the \nindividual healthcare facilities and healthcare professionals in Saudi Arabia. CBAHI provides supplementary', 'individual health

In [23]:
def get_vectorstore(text_chunks):
    # embeddings = OpenAIEmbeddings()
    embeddings = HuggingFaceInstructEmbeddings(model_name="hkunlp/instructor-xl")
    vectorstore = FAISS.from_texts(texts=text_chunks, embedding=embeddings)
    return vectorstore


vectorstore = get_vectorstore(loaded_chunks)
print(vectorstore)
print(type(vectorstore))

/Users/alwaleedalmajlad/Desktop/training/Projects/chatbot GPT/chatbot/lib/python3.11/site-packages/InstructorEmbedding/instructor.py:7: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import trange


load INSTRUCTOR_Transformer


/Users/alwaleedalmajlad/Desktop/training/Projects/chatbot GPT/chatbot/lib/python3.11/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()


max_seq_length  512
<class 'langchain.vectorstores.faiss.FAISS'>


In [24]:
# save the vectorstore to a file
def save_vectorstore(vectorstore, filename):
    with open(filename, 'wb') as file:
        pickle.dump(vectorstore, file)

# Save the vectorstore to a file
save_vectorstore(vectorstore, 'vectorstore.pkl')


In [25]:
def load_vectorstore(filename):
    with open(filename, 'rb') as file:
        return pickle.load(file)

# Load the vectorstore from the file
loaded_vectorstore = load_vectorstore('vectorstore.pkl')
print(loaded_vectorstore)